In [ ]:
!pip install transformers
!pip install torch


In [ ]:
!pip install transformers
!pip install torch
import json

with open('tamilqa (1).json', 'r') as file:
    data = json.load(file)

print(data)


[{'ID': 0, 'Context': '"Hṛṣīkeśa" (சமக்கிருதம்: हृषीकेश) என்பது \'புலன்களின் கடவுள்\' என்ற பொருள் கொண்ட விஷ்ணுவின் பெயராகும். ரிஷிகேஷ் என்பது வட இந்தியாவில் இமாலய மலைத்தொடர் வரிசையில் அமைந்திருக்கும் இந்துக்களின் புனித நகரமாகும். \'ரப்யா ரிஷியின்\' தவத்தின் (சுய-புலனடக்கம்) காரணமாக விஷ்ணுவானவர் கடவுள் ரிஷிகேஷாக அவருக்கு தோன்றியதன் நினைவாக இந்த இடம் அந்தப் பெயரைப் பெற்றிருக்கிறது. ஸ்கந்த புராணத்தில், கடவுள் விஷ்ணு ஒரு மாமரத்தின் கீழே தோன்றியதால் இந்தப் பகுதி \'குப்ஜம்ராக்\' என்று அறியப்படுகிறது. வரலாற்று ரீதியாக, ரிஷிகேஷ் சிவனின் உறைவிடமான புராண ரீதியான \'கேதர்கண்ட்\'டின் (இப்போது கர்வால்) ஒரு பகுதியாக இருந்து வந்திருக்கிறது. இலங்கையின் அரசனான ராவணனைக் கொன்றதற்காக கடவுள் ராமன் இங்கு பிராயச்சித்தம் செய்து கொண்டதாக வரலாறு குறிப்பிடுகிறது;  அவருடைய இளைய சகோதரனான லட்சுமணன் இதே இடத்தில்தான் கங்கையைக் கடந்தார். இந்த இடத்தில்தான் இப்போது கயிற்றைப் பயன்படுத்திச் செல்லக்கூடிய \'லக்ஷ்மன் ஜூலா\' (लक्ष्मण झूला) பாலம் உள்ளது. ஸ்கந்த புராணத்தில் வரும் \'கேதர் கந்த்\' என்பதும் இதே இடத்தில் இந்திரகுந்த

In [ ]:
import json
from transformers import BertTokenizer, BertForQuestionAnswering, TrainingArguments, Trainer
import torch

# Load tokenizer and model
tokenizer = BertTokenizer.from_pretrained('bert-base-multilingual-cased')
model = BertForQuestionAnswering.from_pretrained('bert-base-multilingual-cased')


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(
Some weights of BertForQuestionAnswering were not initialized from the model checkpoint at 

In [ ]:
training_args = TrainingArguments(
    output_dir='./results',
    num_train_epochs=3,
    per_device_train_batch_size=8,
    warmup_steps=500,
    weight_decay=0.01,
    logging_dir='./logs',
    logging_steps=10,
)

In [ ]:
import torch
from torch.utils.data import Dataset

class QADataset(Dataset):
    def __init__(self, encodings, start_positions, end_positions):
        self.encodings = encodings
        self.start_positions = start_positions
        self.end_positions = end_positions

    def __len__(self):
        return len(self.start_positions)

    def __getitem__(self, idx):
        item = {key: torch.tensor(val[idx]) for key, val in self.encodings.items()}
        item['start_positions'] = torch.tensor(self.start_positions[idx])
        item['end_positions'] = torch.tensor(self.end_positions[idx])
        return item

def encode_examples(data):
    encodings = tokenizer(
        [d['Context'] for d in data],
        [d['Question'] for d in data],
        truncation=True,
        padding=True,
        max_length=512,
        return_tensors="pt"
    )

    start_positions = []
    end_positions = []

    for d in data:
        if d['Answer_Start'] is not None and d['Answer_Text']:
            start_pos = d['Answer_Start']
            end_pos = start_pos + len(d['Answer_Text']) - 1
            start_positions.append(start_pos)
            end_positions.append(end_pos)
        else:
            print(f"Skipping entry with missing answer: {d}")
            start_positions.append(0)
            end_positions.append(0)

    dataset = QADataset(encodings, start_positions, end_positions)
    return dataset


encoded_data = encode_examples(data)


trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=encoded_data,
)

trainer.train()


Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pai

Skipping entry with missing answer: {'ID': 3, 'Context': '"Hṛṣīkeśa" (சமக்கிருதம்: हृषीकेश) என்பது \'புலன்களின் கடவுள்\' என்ற பொருள் கொண்ட விஷ்ணுவின் பெயராகும். ரிஷிகேஷ் என்பது வட இந்தியாவில் இமாலய மலைத்தொடர் வரிசையில் அமைந்திருக்கும் இந்துக்களின் புனித நகரமாகும். \'ரப்யா ரிஷியின்\' தவத்தின் (சுய-புலனடக்கம்) காரணமாக விஷ்ணுவானவர் கடவுள் ரிஷிகேஷாக அவருக்கு தோன்றியதன் நினைவாக இந்த இடம் அந்தப் பெயரைப் பெற்றிருக்கிறது. ஸ்கந்த புராணத்தில், கடவுள் விஷ்ணு ஒரு மாமரத்தின் கீழே தோன்றியதால் இந்தப் பகுதி \'குப்ஜம்ராக்\' என்று அறியப்படுகிறது. வரலாற்று ரீதியாக, ரிஷிகேஷ் சிவனின் உறைவிடமான புராண ரீதியான \'கேதர்கண்ட்\'டின் (இப்போது கர்வால்) ஒரு பகுதியாக இருந்து வந்திருக்கிறது. இலங்கையின் அரசனான ராவணனைக் கொன்றதற்காக கடவுள் ராமன் இங்கு பிராயச்சித்தம் செய்து கொண்டதாக வரலாறு குறிப்பிடுகிறது;  அவருடைய இளைய சகோதரனான லட்சுமணன் இதே இடத்தில்தான் கங்கையைக் கடந்தார். இந்த இடத்தில்தான் இப்போது கயிற்றைப் பயன்படுத்திச் செல்லக்கூடிய \'லக்ஷ்மன் ஜூலா\' (लक्ष्मण झूला) பாலம் உள்ளது. ஸ்கந்த புராணத்தில் வரும் \'கேதர் கந்த்\

<ipython-input-8-00e7fc54412c>:14: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  item = {key: torch.tensor(val[idx]) for key, val in self.encodings.items()}


In [ ]:
# Saving the model and tokenizer
model.save_pretrained('./trained_model')
tokenizer.save_pretrained('./trained_model')


In [ ]:
from google.colab import files
import shutil

# Zip the saved model folder
shutil.make_archive('trained_model', 'zip', './trained_model')

# Download the zipped model
files.download('trained_model.zip')
